## Neural Network

This jupyter notebook implements the neural network model using convolutional layers

In [53]:
#Import libraries

from torchvision.io import read_image
from torch.utils.data import DataLoader
import torchvision.transforms as T
import torch 
import torch.nn as nn # basic building block for neural neteorks
import torch.nn.functional as F # import convolution functions like Relu
import torch.optim as optim # optimzer
import os
from sklearn.metrics import recall_score, accuracy_score, f1_score
import numpy as np

from XRayDataset import XRayDataset
from dataloader import train_path, test_path, val_path

In [54]:
class CustomNeuralNetwork(nn.Module):
    def __init__(self):
        super().__init__()
        
        self.LeNet = nn.Sequential(     
            # convolutional layers            
            nn.Sequential(                                            # FIRST LAYER: (INPUT LAYER)
              nn.Conv2d(1, 6, kernel_size=5, stride=1, padding=0),    # CONVOLUTION 
              nn.BatchNorm2d(6),
              nn.ReLU(),
              nn.MaxPool2d(kernel_size=2, stride=2)),                 # POOLING
            nn.Sequential(                                            # SECOND LAYER: HIDDEN LAYER 1
              nn.Conv2d(6, 16, kernel_size=5, stride=1, padding=0),   # CONVOLUTION 
              nn.BatchNorm2d(16),
              nn.ReLU(),
              nn.MaxPool2d(kernel_size=2, stride=2)),                 # POOLING
            # fully connected layers
            nn.Flatten(),
            nn.Linear(16 * 125 * 125, 400),                            # THIRD LAYER: LINEAR YEAR, HIDDEN LAYER 2
            nn.ReLU(),                                                # HIDDEN LAYER's ACTIVATION FUNCION
            nn.Linear(400, 10)                                        # OUTPUT LAYER
        )

    def forward(self, x):
        out = self.LeNet(x)
        print("OUT: ", out)
        return out



In [55]:
model = CustomNeuralNetwork()

In [56]:
#Dataloader code from Checkpoint #1

resize = T.Compose([
            T.ToPILImage(), 
            T.Grayscale(num_output_channels=1),
            T.Resize((int(512), int(512))), # Resize the image to match median ratio using median length, we can try later with smaller length 
            T.ToTensor()
        ])
 
transforms = T.Compose([
            T.ToPILImage(), 
            T.Grayscale(num_output_channels=1),
            T.RandomAdjustSharpness(sharpness_factor=10),
            T.ColorJitter(brightness=.5, hue=.3),
            T.Resize((int(512), int(512))),
            # Resize the image to match median ratio using median length 
            T.ToTensor()
        ])
training_data = XRayDataset(train_path, transforms)
val_data = XRayDataset(val_path, resize)
test_data = XRayDataset(test_path, resize)

#Discussion with Ian said to start with small batches (2,4)
#Medium post said do powers of 2 starting with 16 
#I'll go with middle point and do batch = 8
#https://medium.com/data-science-365/determining-the-right-batch-size-for-a-neural-network-to-get-better-and-faster-results-7a8662830f15

batch_s = 16

train_dataloader = DataLoader(training_data, batch_size=batch_s, shuffle=True)
val_dataloader = DataLoader(val_data, batch_size=batch_s, shuffle=True)
test_dataloader = DataLoader(test_data, batch_size=batch_s, shuffle=True)

# data_inputs, data_labels = next(iter(train_dataloader))

# print("Data inputs", data_inputs.shape, "\n", data_inputs)
# print("Data labels", data_labels.shape, "\n", data_labels)


In [57]:
# 3: Define a Loss function and optimizer
criterion = nn.CrossEntropyLoss() #a.Change the cross entropy of the original code to NLL 
#which we have used before for binary classification
#b. 
optimizer = optim.SGD(model.parameters(), lr=0.001, momentum=0.9)

In [59]:
# 4: Train and validate the network
EPOCHS = 1

train_losses = []
train_accuracies = []
val_losses = []
val_accuracies = []
total_correct = 0
total_predicted = 0
# Iterate over the dataloader and print the first few batches
for i, (inputs, labels) in enumerate(train_dataloader):
    print(f"Batch {i}: Inputs shape = {inputs.shape}, Labels = {labels}")
    if i == 4:
        break  # Stop after printing the first few batches

for _ in range(EPOCHS):
    # TRAIN
    model.train()  # Make sure gradient tracking is on, and do a pass over the data
    running_loss = 0.0
    y_true = []
    y_predict = []
    for i, data in enumerate(train_dataloader):
        # get the inputs; data is a list of [inputs, labels]
        inputs, labels = data
        optimizer.zero_grad()  # zero the parameter gradients
        outputs = model(inputs)  # forward pass
        label_dict = {"PNEUMONIA": 0, "NORMAL": 1}
        labels_tensor = torch.tensor([label_dict[label] for label in labels])
        print("output: ", outputs)
        print("labels: ", labels_tensor)
        loss = criterion(outputs, labels_tensor)  # calculate loss
        print("LOSS: ", loss)
        loss.backward()  # backward pass
        optimizer.step()  # update weights

        # keep track of the loss
        running_loss += loss.item()
        # _, predicted = torch.max(outputs.data, 1)
        ypred_batch = np.argmax(outputs.detach().numpy(), axis=1)
        # total_correct += (predicted == labels_tensor).sum().item()
        # total_predicted += len(labels_tensor)
        
        ytrue_batch = labels_tensor.numpy()
        y_predict.extend(ypred_batch)
        y_true.extend(ytrue_batch)
        print("ypred_batch", ypred_batch)
        print("ytrue_batch", ytrue_batch)
        print("y_predict", y_predict)
        print("y_true", y_true)

       
    
    recall = recall_score(y_true, y_predict, average='binary')

    # avg_train_acc = total_correct/total_predicted  # calculate average accuracy metric
    avg_train_acc = recall
    avg_train_loss = running_loss / (i + 1)
    train_losses.append(avg_train_loss)
    train_accuracies.append(avg_train_acc)

    print("train accuracies: ", train_accuracies)
    print("train losess: ", train_losses)





Batch 0: Inputs shape = torch.Size([16, 1, 512, 512]), Labels = ('PNEUMONIA', 'PNEUMONIA', 'NORMAL', 'PNEUMONIA', 'NORMAL', 'PNEUMONIA', 'PNEUMONIA', 'NORMAL', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'NORMAL', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA')
Batch 1: Inputs shape = torch.Size([16, 1, 512, 512]), Labels = ('PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'NORMAL', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'NORMAL', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA')
Batch 2: Inputs shape = torch.Size([16, 1, 512, 512]), Labels = ('PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'NORMAL', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'NORMAL', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'NORMAL', 'PNEUMONIA')
Batch 3: Inputs shape = torch.Size([16, 1, 512, 512]), Labels = ('NORMAL', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'PNEUMONIA', 'NORMAL', 'PNEUM

In [60]:
print("y_predict", y_predict)
print("y_true", y_true)
print("unique predict", np.unique(y_predict))
print("unique true", np.unique(y_true))

y_predict [1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 1, 0, 1, 0, 0, 1, 0, 1, 0, 0, 1, 1, 0, 0, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 0, 0, 0, 1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 1, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0,

In [61]:
print(running_loss)

81.2826999714598


In [62]:
    model.eval()  # we don't want to keep track of the gradients in the validation part
    for i, data in enumerate(val_dataloader):
        inputs, labels = data
        outputs = model(inputs)
        label_dict = {"PNEUMONIA": 0, "NORMAL": 1}
        labels_tensor = torch.tensor([label_dict[label] for label in labels])
        loss = criterion(outputs, labels_tensor)
        val_losses.append(loss.item())
        _, predicted = torch.max(outputs.data, 1)  # get the index of the max log-probability
        total = len(labels)
        correct = (predicted == labels_tensor).sum().item()
        val_accuracies.append(100 * correct / total)

OUT:  tensor([[ 9.3402,  9.6490, -2.3521, -1.9783, -2.5708, -1.6476, -1.4087, -1.8415,
         -2.6350, -1.9665],
        [ 6.4328,  8.3468, -1.7741, -1.2068, -2.2372, -0.7224, -1.0582, -1.8298,
         -1.6932, -1.9183],
        [16.5771,  6.6063, -0.6494, -1.3320, -2.8544, -3.6937, -1.1181, -0.8145,
         -6.3841, -1.6594],
        [10.4878,  6.1137, -1.0620, -1.3720, -2.0677, -1.8389, -0.9720, -0.9491,
         -3.4681, -1.3433],
        [ 8.2174,  9.0606, -2.3070, -1.8250, -2.3332, -1.2579, -1.7047, -1.7936,
         -2.1127, -1.9050],
        [ 8.8739,  8.2025, -1.9252, -1.4439, -2.2552, -1.3283, -1.2300, -1.5466,
         -2.6289, -1.7794],
        [10.3183,  6.7537, -1.3823, -1.4154, -2.1273, -1.7488, -1.0189, -0.9443,
         -3.4894, -1.3737],
        [ 9.3407,  5.4098, -1.0113, -0.9929, -1.8646, -1.5767, -1.0823, -0.6330,
         -2.9968, -1.6650],
        [ 7.6276,  8.9619, -2.0999, -1.4762, -2.3677, -0.9272, -1.4026, -1.9484,
         -1.9415, -1.6241],
        [18.0

In [63]:
print(val_accuracies)

[93.75]


In [64]:
#5. Test model
with torch.no_grad():
    total = 0
    correct = 0
    for i, data in enumerate(test_dataloader):
        inputs, labels = data
        outputs = model(inputs)
        _, predicted = torch.max(outputs.data, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum().item()
        acc = correct / total
    

OUT:  tensor([[ 7.7834,  7.6482, -1.6948, -1.6396, -1.8938, -1.4991, -1.1229, -1.3243,
         -2.1899, -1.5552],
        [17.0020,  6.2490, -0.2513, -1.1064, -2.8574, -3.6053, -1.0398, -0.8120,
         -6.6954, -1.7261],
        [12.3214,  5.8181, -1.1254, -1.1580, -2.2297, -2.3510, -0.7985, -1.2401,
         -4.3428, -1.3660],
        [14.9173,  5.0431, -0.3645, -0.9876, -2.5829, -3.1735, -0.6580, -1.3223,
         -6.2088, -1.2839],
        [ 7.4489,  6.8375, -1.6061, -1.4152, -2.2734, -1.0990, -1.2364, -1.4699,
         -1.9549, -1.3205],
        [12.4670,  6.4137, -1.0027, -1.3853, -2.4168, -2.5203, -1.0320, -0.9492,
         -4.2398, -1.2732],
        [10.4880,  7.0389, -1.5066, -1.4909, -2.2382, -1.9295, -0.9565, -1.2564,
         -3.3903, -1.4620],
        [14.8315,  6.0358, -0.6979, -1.0737, -2.4235, -2.9997, -0.9960, -0.8720,
         -5.5642, -1.6449],
        [14.0915,  5.6007, -0.4895, -1.1630, -2.2615, -3.1810, -1.1157, -0.4483,
         -5.3559, -1.5466],
        [ 9.2

AttributeError: 'tuple' object has no attribute 'size'

In [ ]:
# Activation Functions
# ReLU
# x being the tensor
y = torch.relu(x)